In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
import torchvision.datasets as datasets
from torch.utils.data import DataLoader, Subset
from torchvision import models

In [2]:
# Define class labels to include
selected_classes = {'bird': 2, 'cat': 3, 'deer': 4, 'dog': 5, 'frog': 6, 'horse': 7}
num_classes = len(selected_classes)

class_mapping = {2: 0, 3: 1, 4: 2, 5: 3, 6: 4, 7: 5}  # Remap to 0-5 range

def get_filtered_dataset(train=True):
    transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
    ])
    dataset = datasets.CIFAR10(root='./data', train=train, download=True, transform=transform)

    filtered_data = [(img, class_mapping[label]) for img, label in dataset if label in class_mapping]
    return torch.utils.data.TensorDataset(
        torch.stack([img for img, _ in filtered_data]),
        torch.tensor([label for _, label in filtered_data])
    )

In [33]:
# Load filtered datasets
train_dataset = get_filtered_dataset(train=True)
val_dataset = get_filtered_dataset(train=False)

# Define DataLoaders
batch_size = 2048
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)

Files already downloaded and verified
Files already downloaded and verified


In [4]:
train_labels = [label for _, label in train_dataset]
val_labels = [label for _, label in val_dataset]

print("Unique labels in train dataset:", max(train_labels))
print("Unique labels in validation dataset:", max(val_labels))

Unique labels in train dataset: tensor(5)
Unique labels in validation dataset: tensor(5)


In [34]:
# Load pre-trained ResNet model and modify classifier
model = models.resnet152(pretrained=True)
for param in model.parameters():
    param.requires_grad = False  # Freeze feature extractor

# Modify the classifier for 6 classes with an additional hidden layer
model.fc = nn.Sequential(
    nn.Linear(model.fc.in_features, 512),
    nn.ReLU(),
    nn.Linear(512, num_classes)
)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.fc.parameters(), lr=0.005)

In [35]:
# Training function
def train_model(model, train_loader, val_loader, epochs=10):
    for epoch in range(epochs):
        model.train()
        running_loss = 0.0
        for images, labels in train_loader:
            images, labels = images.to(device), labels.to(device)
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item()

        print(f"Epoch [{epoch+1}/{epochs}], Loss: {running_loss/len(train_loader):.4f}")
    print("Training complete!")

# Train the model
train_model(model, train_loader, val_loader, epochs=50)

Epoch [1/50], Loss: 3.5701
Epoch [2/50], Loss: 1.5634
Epoch [3/50], Loss: 1.3792
Epoch [4/50], Loss: 1.2970
Epoch [5/50], Loss: 1.2437
Epoch [6/50], Loss: 1.2093
Epoch [7/50], Loss: 1.1940
Epoch [8/50], Loss: 1.1638
Epoch [9/50], Loss: 1.1560
Epoch [10/50], Loss: 1.1454
Epoch [11/50], Loss: 1.1354
Epoch [12/50], Loss: 1.1121
Epoch [13/50], Loss: 1.1029
Epoch [14/50], Loss: 1.0843
Epoch [15/50], Loss: 1.0740
Epoch [16/50], Loss: 1.0754
Epoch [17/50], Loss: 1.0622
Epoch [18/50], Loss: 1.0484
Epoch [19/50], Loss: 1.0432
Epoch [20/50], Loss: 1.0280
Epoch [21/50], Loss: 1.0292
Epoch [22/50], Loss: 1.0211
Epoch [23/50], Loss: 1.0173
Epoch [24/50], Loss: 1.0112
Epoch [25/50], Loss: 1.0140
Epoch [26/50], Loss: 0.9901
Epoch [27/50], Loss: 0.9816
Epoch [28/50], Loss: 0.9871
Epoch [29/50], Loss: 0.9813
Epoch [30/50], Loss: 0.9792
Epoch [31/50], Loss: 0.9712
Epoch [32/50], Loss: 0.9599
Epoch [33/50], Loss: 0.9558
Epoch [34/50], Loss: 0.9523
Epoch [35/50], Loss: 0.9444
Epoch [36/50], Loss: 0.9516
E

In [29]:
# Save the model as pth file
torch.save(model.state_dict(), 'model.pth')

In [36]:
def test_model(model, test_loader):
    model.eval()  # Set to evaluation mode
    correct = 0
    total = 0
    test_loss = 0.0
    with torch.no_grad():  # No need to track gradients
        for images, labels in test_loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            test_loss += loss.item()

            _, predicted = torch.max(outputs, 1)  # Get class with highest probability
            correct += (predicted == labels).sum().item()
            total += labels.size(0)

    avg_loss = test_loss / len(test_loader)
    accuracy = 100 * correct / total
    print(f"Test Loss: {avg_loss:.4f}, Test Accuracy: {accuracy:.2f}%")
    return avg_loss, accuracy

# Run the test loop
test_model(model, train_loader)

Test Loss: 0.8585, Test Accuracy: 67.88%


(0.8585072080294291, 67.88)